This notebook focuses on extracting data from a MongoDB NoSQL collection and CSV files stored in the Data Lake. It performs necessary data cleaning and joins the datasets to produce a unified final output table.

In [0]:
import pandas as pd

In [0]:
from pyspark.sql import functions as F
from pyspark.sql.functions import col, to_date, datediff, current_date


In [0]:
# Getting the access to csv file from the Azure Data Lake through Service Principle
storage_account = ""
application_id = ""
directory_id = ""
# service_credential = dbutils.secrets.get(scope="<scope>",key="<service-credential-key>")

spark.conf.set(f"fs.azure.account.auth.type.{storage_account}.dfs.core.windows.net", "OAuth")
spark.conf.set(f"fs.azure.account.oauth.provider.type.{storage_account}.dfs.core.windows.net", "org.apache.hadoop.fs.azurebfs.oauth2.ClientCredsTokenProvider")
spark.conf.set(f"fs.azure.account.oauth2.client.id.{storage_account}.dfs.core.windows.net", application_id)
spark.conf.set(f"fs.azure.account.oauth2.client.secret.{storage_account}.dfs.core.windows.net", "")
spark.conf.set(f"fs.azure.account.oauth2.client.endpoint.{storage_account}.dfs.core.windows.net", f"https://login.microsoftonline.com/{directory_id}/oauth2/token")

In [0]:
# Reading all the csv files
base_path = "abfss://olistdata@olistecommadls.dfs.core.windows.net/bronze/"
orders_path = base_path + "olist_orders_dataset.csv"
customers_path = base_path + "olist_customers_dataset.csv"
geolocation_path = base_path + "olist_geolocation_dataset.csv"
items_path = base_path + "olist_order_items_dataset.csv"
payments_path = base_path + "olist_order_payments_dataset"
products_path = base_path + "olist_products_dataset.csv"
sellers_path = base_path + "olist_sellers_dataset.csv"
order_review_path = base_path + "olist_order_reviews_dataset.csv"   
# product_translation_path = base_path + "product_category_name_translation.csv"

customer_df = spark.read.format("csv").option("header", "true").option("inferSchema", "true").load(customers_path)
geolocation_df = spark.read.format("csv").option("header", "true").option("inferSchema", "true").load(geolocation_path)
orders_df = spark.read.format("csv").option("header", "true").option("inferSchema", "true").load(orders_path)
items_df = spark.read.format("csv").option("header", "true").option("inferSchema", "true").load(items_path)   
payments_df = spark.read.format("csv").option("header", "true").option("inferSchema", "true").load(payments_path)
products_df  = spark.read.format("csv").option("header", "true").option("inferSchema", "true").load(products_path)
sellers_df = spark.read.format("csv").option("header", "true").option("inferSchema", "true").load(sellers_path)
order_review_df = spark.read.format("csv").option("header", "true").option("inferSchema", "true").load(order_review_path)



In [0]:
import pymongo

Getting NoSQL data directly from the MongoDB database

In [0]:
# importing module
from pymongo import MongoClient

hostname = "kpb69.h.filess.io"
database = "olistDataNoSQL_readyplain"
port = "27018"
username = "olistDataNoSQL_readyplain"
password = "fb90d98a69dea27adc3be65ab015df5f64a080c7"

uri = "mongodb://" + username + ":" + password + "@" + hostname + ":" + port + "/" + database

# Connect with the portnumber and host
client = MongoClient(uri)

# Access database
mydatabase = client[database]


In [0]:
collection = mydatabase["product_categories"]
mongo_data = pd.DataFrame(list(collection.find()))

In [0]:
mongo_data.drop('_id', axis=1, inplace=True)

In [0]:
mongo_spark_df = spark.createDataFrame(mongo_data)

##Cleaning data

In [0]:
orders_df.printSchema()

root
 |-- order_id: string (nullable = true)
 |-- customer_id: string (nullable = true)
 |-- order_status: string (nullable = true)
 |-- order_purchase_timestamp: timestamp (nullable = true)
 |-- order_approved_at: timestamp (nullable = true)
 |-- order_delivered_carrier_date: timestamp (nullable = true)
 |-- order_delivered_customer_date: timestamp (nullable = true)
 |-- order_estimated_delivery_date: timestamp (nullable = true)



In [0]:
orders_df.count()

99441

In [0]:
display(orders_df.select([F.sum(F.col(c).isNull().cast("int")).alias(c) for c in orders_df.columns]))

order_id customer_id order_status order_purchase_timestamp order_approved_at order_delivered_carrier_date order_delivered_customer_date order_estimated_delivery_date 0 0 0 0 160 1783 2965 0

In [0]:
#Removing nulls and dropping duplicates
def clean_data(df, name):
    df_cleaned = df.na.drop(how ="all")
    return df_cleaned.dropDuplicates()

In [0]:
orders_clean_df = clean_data(orders_df, "orders_df")
customer_clean_df = clean_data(customer_df, "customer_df")
geolocation_clean_df = clean_data(geolocation_df, "geolocation_df")
items_clean_df = clean_data(items_df, "items_df")
payments_clean_df = clean_data(payments_df, "payments_df")
products_clean_df = clean_data(products_df, "products_df")
sellers_clean_df = clean_data(sellers_df, "sellers_df")
order_review_df = clean_data(order_review_df, "order_review_df")


# display(orders_clean_df.select([F.sum(F.col(c).

In [0]:
display(orders_clean_df.select([F.sum(F.col(c).isNull().cast("int")).alias(c) for c in orders_df.columns]))

order_id customer_id order_status order_purchase_timestamp order_approved_at order_delivered_carrier_date order_delivered_customer_date order_estimated_delivery_date 0 0 0 0 160 1783 2965 0

In [0]:
# Convert Date time stamp to Date Column

orders_clean_df = orders_clean_df.withColumn("order_purchase_date", to_date(col("order_purchase_timestamp"))).withColumn("order_approved_date", to_date(col("order_approved_at"))).withColumn("order_delivered_carrier_date", to_date(col("order_delivered_carrier_date"))).withColumn("order_delivered_customer_date", to_date(col("order_delivered_customer_date"))).withColumn("order_estimated_delivery_date", to_date(col("order_estimated_delivery_date")))

In [0]:
# Calculate Delivery and delay times

orders_clean_df = orders_clean_df.withColumn("actual_delivery_time", datediff(col("order_delivered_customer_date"), col("order_purchase_date"))).withColumn("estimated_delivery_time", datediff(col("order_estimated_delivery_date"), col("order_purchase_date")))
orders_clean_df = orders_clean_df.withColumn("delay time", F.when(col("actual_delivery_time") > F.col("estimated_delivery_time"), col("actual_delivery_time") - col("estimated_delivery_time")).otherwise(0))

In [0]:
# display(orders_clean_df)

In [0]:
# Joining
orders_customer_df = orders_clean_df.join(customer_clean_df, orders_clean_df.customer_id == customer_clean_df.customer_id, "left")
orders_payments_df = orders_customer_df.join(payments_clean_df, orders_customer_df.order_id == payments_clean_df.order_id, "left")
orders_items_df = orders_payments_df.join(items_clean_df, "order_id", "left")
orders_products_df = orders_items_df.join(products_clean_df, orders_items_df.product_id == products_clean_df.product_id, "left")
final_df = orders_products_df.join(sellers_clean_df, orders_items_df.seller_id == sellers_clean_df.seller_id, "left")



In [0]:
final_df = final_df.join(mongo_spark_df, "product_category_name", "left")
display(final_df)

product_category_name order_id customer_id order_status order_purchase_timestamp order_approved_at order_delivered_carrier_date order_delivered_customer_date order_estimated_delivery_date order_purchase_date order_approved_date actual_delivery_time estimated_delivery_time delay time customer_id customer_unique_id customer_zip_code_prefix customer_city customer_state order_id payment_sequential payment_type payment_installments payment_value order_item_id product_id seller_id shipping_limit_date price freight_value product_id product_name_lenght product_description_lenght product_photos_qty product_weight_g product_length_cm product_height_cm product_width_cm seller_id seller_zip_code_prefix seller_city seller_state product_category_name_english bebes acce194856392f074dbf9dada14d8d82 7e20bf5ca92da68200643bda76c504c6 delivered 2018-06-04T00:00:13Z 2018-06-05T00:35:10Z 2018-06-05 2018-06-16 2018-07-18 2018-06-04 2018-06-05 12 44 0 7e20bf5ca92da68200643bda76c504c6 576ea0cab426cd8a00fad9a9c90a4494 41213 salvador BA acce194856392f074dbf9dada14d8d82 1 credit_card 10 227.679993 2 9451e630d725c4bb7a5a206b48b99486 d673a59aac7a70d8b01e6902bf090a11 2018-06-13T00:35:10Z 39.5 48.64 9451e630d725c4bb7a5a206b48b99486 52 300 1 350 31 10 12 d673a59aac7a70d8b01e6902bf090a11 14940 ibitinga SP baby bebes acce194856392f074dbf9dada14d8d82 7e20bf5ca92da68200643bda76c504c6 delivered 2018-06-04T00:00:13Z 2018-06-05T00:35:10Z 2018-06-05 2018-06-16 2018-07-18 2018-06-04 2018-06-05 12 44 0 7e20bf5ca92da68200643bda76c504c6 576ea0cab426cd8a00fad9a9c90a4494 41213 salvador BA acce194856392f074dbf9dada14d8d82 1 credit_card 10 227.679993 1 d70f38e7f79c630f8ea00c993897042c 977f9f63dd360c2a32ece2f93ad6d306 2018-06-13T00:35:10Z 90.9 48.64 d70f38e7f79c630f8ea00c993897042c 53 233 1 10950 41 40 40 977f9f63dd360c2a32ece2f93ad6d306 14910 tabatinga SP baby cama_mesa_banho 1d067305b599c1e0dceb3864056ea527 0489975a325480c9e385e9f135bb13c3 delivered 2018-02-14T13:05:17Z 2018-02-14T13:15:38Z 2018-02-20 2018-03-09 2018-03-09 2018-02-14 2018-02-14 23 23 0 0489975a325480c9e385e9f135bb13c3 b577af9a54b023b4bcc51f69bb937f1c 14406 franca SP 1d067305b599c1e0dceb3864056ea527 1 credit_card 5 170.429993 1 2a2d22ae30e026f1893083c8405ca522 1a3df491d1c4f1589fc2b934ada68bf2 2018-02-22T12:15:38Z 148.9 21.53 2a2d22ae30e026f1893083c8405ca522 60 744 2 8350 50 27 38 1a3df491d1c4f1589fc2b934ada68bf2 89224 joinville SC bed_bath_table perfumaria 6942b8da583c2f9957e990d028607019 52006a9383bf149a4fb24226b173106f shipped 2018-01-10T11:33:07Z 2018-01-11T02:32:30Z 2018-01-11 null 2018-02-07 2018-01-10 2018-01-11 null 28 0 52006a9383bf149a4fb24226b173106f 528b011eb7fab3d59c336cc7248eed3a 38600 paracatu MG 6942b8da583c2f9957e990d028607019 1 boleto 1 69.1200027 1 ee0c1cf2fbeae95205b4aa506f1469f0 cc419e0650a3c5ba77189a1882b7556a 2018-01-18T02:32:30Z 53.99 15.13 ee0c1cf2fbeae95205b4aa506f1469f0 44 334 1 200 16 16 13 cc419e0650a3c5ba77189a1882b7556a 9015 santo andre SP perfumery null 6f841dde94727854eaff3f66432c80ea a9c9532060c9d245f06526c633d2dfba delivered 2018-01-02T19:20:35Z 2018-01-02T19:32:22Z 2018-01-03 2018-01-27 2018-02-05 2018-01-02 2018-01-02 25 34 0 a9c9532060c9d245f06526c633d2dfba 5f38cc36e507c4d880489be38964af19 27262 volta redonda RJ 6f841dde94727854eaff3f66432c80ea 1 credit_card 3 192.949997 1 c600d7f13104e8db2ca2b9fa78581409 f18112da765e0971ca5d510dec322bdd 2018-01-08T19:32:22Z 168.9 24.05 c600d7f13104e8db2ca2b9fa78581409 null null null 2400 42 15 27 f18112da765e0971ca5d510dec322bdd 88351 brusque SC null beleza_saude ca290a06ee0945b956f79c93b5191633 acd575d7382968889f41a5a3f37510dd delivered 2018-04-09T22:02:30Z 2018-04-09T23:10:27Z 2018-04-10 2018-04-25 2018-05-10 2018-04-09 2018-04-09 16 31 0 acd575d7382968889f41a5a3f37510dd 323c4e9d78f774df9255793377ce636e 77645 lajeado TO ca290a06ee0945b956f79c93b5191633 1 credit_card 1 175.100006 1 2948658cb6abc82847412be7201bfc4c 955fee9216a65b617aa5c0531780ce60 2018-04-15T23:10:27Z 120.0 55.1 2948658cb6abc82847412be7201bfc4c 59 1030 5 3500 36 25 21 95

Databricks visualization. Run in Databricks to view.

In [0]:
final_cleaned_df = final_df.drop(*[col for col in final_df.columns if "__" in col])
# display(final_cleaned_df)

In [0]:
def remove_duplicate_cols(df):
    columns = df.columns
    seen_cols = set()
    cols_to_drop = []
    for col in columns:
        if col in seen_cols:
            cols_to_drop.append(col)
        else:
            seen_cols.add(col)
    return df.drop(*cols_to_drop)
final_cleaned_df = remove_duplicate_cols(final_cleaned_df)
# display(final_cleaned_df)

In [0]:
final_cleaned_df.write.mode("overwrite").parquet("abfss://olistdata@olistecommadls.dfs.core.windows.net/silver/")